# Analyzing results from humann3 run on time series MTX datasets previously analyzed in the paper: [Dissection of Microbial Community Functions during a Cyanobacterial Bloom in the Baltic Sea via Metatranscriptomics](https://www.frontiersin.org/articles/10.3389/fmars.2018.00055/full)

BioProject PRJNA320636: Searchable via: https://sra-explorer.info/  

**NOTE:** The following results were obtained by running HumanN3 with our custom DB: prok_euk_plankt_clustered_db_v2.1_201901b.dmnd  

Author: jayson.gutierrez@vliz.be

In [1]:
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
from matplotlib import cm
import seaborn as sns
import colorsys
from matplotlib.collections import PatchCollection

import Bio.SeqIO as bioseqio
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
#from Bio.Alphabet import IUPAC
from Bio import Entrez

from ete3 import NCBITaxa
from taxonomy_ranks import TaxonomyRanks

from subprocess import Popen, call, STDOUT, PIPE
import os
import shutil
import pandas as pd
import numpy as np
import matplotlib
import json
import glob
import re
import gzip
import sys
import csv
import time
import io
import pathlib
from collections import OrderedDict

from IPython.display import Image
from itertools import combinations
import itertools

In [2]:
#Customized functions for parsing and visualizing output data from HumanN-based profiling + our custo DB
from HumanN_data_processing import *

In [3]:
import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px
###Uncomment below if necessary
rendef = "png" #"pdf" 
fig_renderer = pio.renderers[rendef]
fig_renderer.width = 1000
fig_renderer.height = 1000
pio.renderers.default = rendef

In [4]:
from sklearn.manifold import MDS
import sklearn.datasets as dt
from sklearn.metrics.pairwise import manhattan_distances, euclidean_distances
from scipy.spatial import distance

In [5]:
import warnings
warnings.filterwarnings("ignore")

In [6]:
!which python

/apps/gent/RHEL8/zen3-ampere-ib/software/Python/3.9.5-GCCcore-10.3.0/bin/python


In [7]:
matplotlib.rcParams['savefig.dpi'] = 900
matplotlib.rcParams['figure.dpi'] = 1000
sns.set_style("whitegrid", {'axes.grid' : False})
sns.set_context("paper")
sns.set(font='serif')
# sns.set_style("white", {
#         "font.family": "serif",
#         "font.serif": ["Times", "Palatino", "serif"]
#     })
sns.set_style('ticks')

In [8]:
# ###Utility functions

def format_tax_lbl(taxid = '94617', tax_lvl=[]):
    """Function to properly format taxonomic labels compatible with HumanN"""
    
    try:
        tax_lvls_lbls = ['superkingdom', 'phylum', 'class', 'order', 'family', 'genus', 'species']
        rank_taxon = TaxonomyRanks(taxid)
        rank_taxon.get_lineage_taxids_and_taxanames()
        rank_dict =  list(rank_taxon.lineages.values())[0]
        tax_tree = list(rank_taxon.lineages.values())[0]
        if(len(tax_lvl)==0):
            return tax_tree
        else:
            return [tax_tree[k][0] for k in tax_lvl]
    except:
        pass
    
def broad_tax_classif(pcl):
    '''Function to obtain a broader tax classification'''
    if 'Dinophyceae' in pcl:
        return 'Dinophyceae'
    elif 'Bacillariophyta' in pcl:
        return 'Bacillariophyta'
    elif 'Haptophyta' in pcl:
        return 'Haptophyta'
    elif 'Arthropoda' in pcl:
        return 'Arthropoda'
    elif 'Chlorophyta' in pcl:
        return 'Chlorophyta'
    elif 'Cyanobacteria' in pcl:
        return 'Cyanobacteria'
    elif 'Foraminifera' in pcl:
        return 'Foraminifera'
    elif 'Cryptophyceae' in pcl:
        return 'Cryptophyceae'
    elif 'Proteobacteria' in pcl:
        return 'Proteobacteria'
    elif 'Bacteroidetes' in pcl:
        return 'Bacteroidetes'
    elif 'Ciliophora' in pcl:
        return 'Ciliophora'
    elif 'Ascomycota' in pcl:
        return 'Ascomycota'
    elif pcl is None:
        'Unclassified'
    else:
        return 'Other'
    
    
def simplify_sample_id(sid):
    if 'Raneafjarden' in sid:
        return 'Raneafjarden'
    elif 'Bottenhavet' in sid:
        return 'Bottenhavet'
    elif 'Lake TorneTrask' in sid:
        return 'Lake TorneTrask'
    elif 'Helcom site 4' in sid:
        return 'Helcom site 4'
    elif 'Oland' in sid:
        return 'Oland'
    elif 'DMU 939' in sid:
        return 'DMU 939'
    elif 'DMU 1005' in sid:
        return 'DMU 1005'
    elif 'Stockholm Archipelago' in sid:
        return 'Stockholm Archipelago'

Loading cpm-normalized gene family abundances with human-readable metabolic rxns 

In [14]:
#Data output from humann run with default DBs (chocophlan + UniRef90 2020b)
cpm_norm_gene_rxn_renamed_df = pd.read_csv("data_PRJNA320636/joint_samples_regrouped2rxn-cpm-named.tsv", sep="\t")
cpm_norm_gene_rxn_renamed_df.head()

# Gene Family  \
0                                           UNMAPPED   
1                                          UNGROUPED   
2  UNGROUPED|g__Acanthamoeba.s__Acanthamoeba_lent...   
3  UNGROUPED|g__Acanthamoeba.s__Acanthamoeba_royr...   
4  UNGROUPED|g__Acaulopage.s__Acaulopage_tetracer...   

   SRR3745322_Abundance-CPM  SRR3745332_Abundance-CPM  \
0             701611.000000             701996.000000   
1             290247.044287             287245.620146   
2                 58.973488                 31.486446   
3                166.003547                 57.815915   
4                  4.143991                  0.660919   

   SRR3745334_Abundance-CPM  SRR3745335_Abundance-CPM  \
0             700130.000000             667032.000000   
1             294320.639705             324172.667925   
2                251.286718                 33.203815   
3                318.235631                 64.058178   
4                  1.008004                  0.705707   

   SRR3745337_Abundance-CPM  SRR3745339_Abundance-CPM  \
0             637193.000000             427345.000000   
1             353483.784647             434448.623768   
2                286.154961                201.019653   
3                329.636311                206.454937   
4                  1.001160                  3.348427   

   SRR3745340_Abundance-CPM  SRR3745341_Abundance-CPM  \
0             798851.000000             666207.000000   
1             189679.123794             324313.350076   
2                523.458779                166.230075   
3                529.205038                300.664463   
4                  1.874512                  2.541319   

   SRR3745343_Abundance-CPM  ...  SRR3747803_Abundance-CPM  \
0             699450.000000  ...             529868.000000   
1             292893.572704  ...             393894.858968   
2                228.019684  ...                  8.069131   
3                179.357755  ...                 22.990488   
4                  1.986250  ...                  3.845298   

   SRR3747804_Abundance-CPM  SRR3747805_Abundance-CPM  \
0             618902.000000             744567.000000   
1             316636.484853             205578.040727   
2                 10.754519                  7.851881   
3                 24.567759                 26.629056   
4                  2.903497                  1.587539   

   SRR3747806_Abundance-CPM  SRR3747807_Abundance-CPM  \
0             685082.000000             778797.000000   
1             256641.300228             193340.732211   
2                  8.229883                 16.358702   
3                 23.683851                 66.822518   
4                  3.487390                  0.000000   

   SRR3747808_Abundance-CPM  SRR3747809_Abundance-CPM  \
0             808278.000000             788070.000000   
1             155600.351013             177326.405508   
2                  9.191166                  9.733929   
3                 79.738183                 26.462728   
4                  2.226626                  0.443289   

   SRR3747810_Abundance-CPM  SRR3747823_Abundance-CPM  \
0             961914.000000             800541.000000   
1              33681.665370             168134.211101   
2                 28.715554                  8.161739   
3                 34.832099                 28.729387   
4                  0.161654                  0.404593   

   SRR3747824_Abundance-CPM  
0             919723.000000  
1              72798.135160  
2                  6.872195  
3                 18.840771  
4                  0.098815  

[5 rows x 66 columns]

In [15]:
#Loading metadata file containing info on site and timing of sampling
metadata_df = pd.read_csv("data_PRJNA320636/sra_explorer_metadata.tsv", sep='\t')[['Accession','Title']]
metadata_df.drop_duplicates(subset='Title', inplace=True)
metadata_df.set_index('Accession',inplace=True)
metadata_df["Station_ID"] = metadata_df["Title"].apply(lambda s: s.split(":")[0])
metadata_df["Station_Name"] = metadata_df["Title"].apply(lambda s: s.split(":")[1])
metadata_df['Location'] = metadata_df['Station_Name'].apply(simplify_sample_id)

In [16]:
#Number of distinct smapling sites/stations
for i in metadata_df['Location'].sort_values().unique():
    print(i)

Bottenhavet
DMU 1005
DMU 939
Helcom site 4
Lake TorneTrask
Oland
Raneafjarden
Stockholm Archipelago


In [17]:
cond_list0 = []
for gf in cpm_norm_gene_rxn_renamed_df['# Gene Family'].values:
    if ('UNMAPPED' in gf) or ('UNGROUPED' in gf):
        cond_list0.append(False)
    else:
        cond_list0.append(True)

#Finally, get a filtered df
index_list0 = cpm_norm_gene_rxn_renamed_df[cond_list0].sum(axis=1).sort_values(ascending=False).index.values
cpm_norm_gene_rxn_renamed_filtered_df = cpm_norm_gene_rxn_renamed_df.iloc[index_list0].reset_index(drop=True)
cpm_norm_gene_rxn_renamed_filtered_df.set_index(keys='# Gene Family', inplace=True)
#Here we further filter the df to keep only entrie linked to a given species
cpm_norm_gene_rxn_renamed_filtered_df2 = cpm_norm_gene_rxn_renamed_filtered_df.iloc[cpm_norm_gene_rxn_renamed_filtered_df.index.map(lambda s: '|g__' in s) ]

In [18]:
print("Total number of enzymes mapped: {}".format(cpm_norm_gene_rxn_renamed_filtered_df2.shape[0]))

Total number of enzymes mapped: 93565


In [19]:
#Let's peek at top 5 most abundant rxns across all samples
cpm_norm_gene_rxn_renamed_filtered_df2.head()

SRR3745322_Abundance-CPM  \
# Gene Family                                                                  
PYRUVFORMLY-RXN: (expasy) Formate C-acetyltrans...                     0.000   
4.1.1.83-RXN: (expasy) 4-hydroxyphenylacetate d...                     0.000   
RXN-20409: (expasy) 4-hydroxyphenylacetate deca...                     0.000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                     0.000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                    70.652   

                                                    SRR3745332_Abundance-CPM  \
# Gene Family                                                                  
PYRUVFORMLY-RXN: (expasy) Formate C-acetyltrans...                      0.00   
4.1.1.83-RXN: (expasy) 4-hydroxyphenylacetate d...                      0.00   
RXN-20409: (expasy) 4-hydroxyphenylacetate deca...                      0.00   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                      0.00   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                    221.12   

                                                    SRR3745334_Abundance-CPM  \
# Gene Family                                                                  
PYRUVFORMLY-RXN: (expasy) Formate C-acetyltrans...                    0.0000   
4.1.1.83-RXN: (expasy) 4-hydroxyphenylacetate d...                    0.0000   
RXN-20409: (expasy) 4-hydroxyphenylacetate deca...                    0.0000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                    0.0000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   74.5174   

                                                    SRR3745335_Abundance-CPM  \
# Gene Family                                                                  
PYRUVFORMLY-RXN: (expasy) Formate C-acetyltrans...                   0.00000   
4.1.1.83-RXN: (expasy) 4-hydroxyphenylacetate d...                   0.00000   
RXN-20409: (expasy) 4-hydroxyphenylacetate deca...                   0.00000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   5.75148   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   5.73410   

                                                    SRR3745337_Abundance-CPM  \
# Gene Family                                                                  
PYRUVFORMLY-RXN: (expasy) Formate C-acetyltrans...                   0.00000   
4.1.1.83-RXN: (expasy) 4-hydroxyphenylacetate d...                   0.00000   
RXN-20409: (expasy) 4-hydroxyphenylacetate deca...                   0.00000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   0.00000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   8.89324   

                                                    SRR3745339_Abundance-CPM  \
# Gene Family                                                                  
PYRUVFORMLY-RXN: (expasy) Formate C-acetyltrans...              114038.73539   
4.1.1.83-RXN: (expasy) 4-hydroxyphenylacetate d...               87595.47819   
RXN-20409: (expasy) 4-hydroxyphenylacetate deca...               87595.47819   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   0.00000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  74.66400   

                                                    SRR3745340_Abundance-CPM  \
# Gene Family                                                                  
PYRUVFORMLY-RXN: (expasy) Formate C-acetyltrans...                  0.000000   
4.1.1.83-RXN: (expasy) 4-hydroxyphenylacetate d...                  0.000000   
RXN-20409: (expasy) 4-hydroxyphenylacetate deca...                  0.000000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  0.000000   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  0.787494   

                                                    SRR3745341_Abundance-CPM  \
# Gene Family                                

#### Now, let's focus on analyzing metabolic pathway abundances across samples and the numerous taxa observed

In [20]:
#First we sort out metadata df based on number of samples collected per station
df_cont = []
for loc_id in metadata_df["Location"].value_counts().index:
    sub_df = metadata_df.query('Location  == "{}"'.format(loc_id)).sort_values('Station_ID')
    sub_df['Location'] = list(map(lambda s: "_".join(s), zip(sub_df['Location'],np.arange(sub_df['Location'].size).astype(str))))
    df_cont.append(sub_df)
    
sorted_metadata_df = pd.concat(df_cont)

In [21]:
table_fid = "data_PRJNA320636/joint_samples_path_abundance-cpm.tsv"
custom_db_pwy_abund_df = reshape_joint_pwy_abund_df(table_fid, "SRR")
custom_db_pwy_abund_df.to_csv("data_PRJNA320636/reshaped_joint_samples_path_abundance-cpm.tsv",sep="\t")
pwy_abund_full = pd.read_csv(table_fid,sep='\t')

In [22]:
#Grab all species-specific pawy abundances
idx2pwy_dict = pwy_abund_full['# Pathway'].to_dict()
idx_list = []
for k in idx2pwy_dict:
    v = idx2pwy_dict[k]
    if (v!='UNMAPPED') and ('UNINTEGRATED' not in v) and ('|g__' in v):
        idx_list.append(k)
        
#Filter out the original pwy abundance df
filtered_pwy_abund_full = pwy_abund_full.iloc[idx_list,:]
filtered_pwy_abund_full.reset_index(drop=True, inplace=True)

old_sample_ids = filtered_pwy_abund_full.iloc[:,1:].columns
new_sampled_ids = list(map(lambda s: s.split("_")[0],old_sample_ids))
#Rename column names
# filtered_pwy_abund_full.rename(columns=dict(zip(old_sample_ids,new_sampled_ids)),inplace=True)
# filtered_pwy_abund_full.rename(columns=sid2data,inplace=True)

#Create intermediary DF to reshape filtered_pwy_abund_full
new_filtered_pwy_abund_full = pd.DataFrame.from_records(filtered_pwy_abund_full['# Pathway'].apply(lambda s: s.split('|')).values, 
                                                        columns=["PWY","Species"]).set_index("PWY")

#Reassign index and first column of filtered_pwy_abund_full
filtered_pwy_abund_full.index = new_filtered_pwy_abund_full.index
filtered_pwy_abund_full['# Pathway'] = new_filtered_pwy_abund_full['Species']
filtered_pwy_abund_full.rename(columns={'# Pathway':'Species'},inplace=True)

#Rename sample ids to station/location
new_sid = {}
for sid in filtered_pwy_abund_full.columns[1:]:
    new_sid[sid] = sorted_metadata_df['Location'].loc[sid.split("_")[0]]
    
filtered_pwy_abund_full.rename(columns=new_sid,inplace=True)

#Sort columns by name
sorted_cols = filtered_pwy_abund_full.columns[1:].sort_values()

filtered_pwy_abund_full = filtered_pwy_abund_full[sorted_cols.insert(0,'Species')]

In [23]:
#Let's sort metabolic pathways based on their aggregated abundance observed across samples and species
agg_pwy_abund = filtered_pwy_abund_full.groupby("PWY").sum().sum(axis=1).sort_values(ascending=False)
#Set a threshold
agg_pwy_abund = agg_pwy_abund[agg_pwy_abund>10]

filtered_pwy_abund_full2 = filtered_pwy_abund_full.loc[agg_pwy_abund.index]

In [24]:
filtered_pwy_abund_full2["Species"].values

array(['g__Anabaena.s__Anabaena_sp_CRKS33',
       'g__Aphanizomenon.s__Aphanizomenon_flos_aquae',
       'g__Corethron.s__Corethron_hystrix__216773', ...,
       'g__Planktomarina.s__Planktomarina_temperata',
       'g__Nodularia.s__Nodularia_spumigena',
       'g__Planktomarina.s__Planktomarina_temperata'], dtype=object)

In [25]:
#Add extra taxonomic classification to track down lower levels in the tree
ncbi_taxids_series = filtered_pwy_abund_full2["Species"].map(lambda s: s.split('__')[-1].replace('_', ' '))
tax_lvls = ['phylum','class']
extra_tax_lvls_series = ncbi_taxids_series.map(lambda s: format_tax_lbl(s, tax_lvls))
#Adding to main metabolic pathway DF a broad taxonomic group
tax_group_cont = []
for w in extra_tax_lvls_series:
    if(w is not None):
        tax_group_cont.append(broad_tax_classif(w))
    else:
        tax_group_cont.append("Unclassified")

filtered_pwy_abund_full2["TaxGroup"] = tax_group_cont

#Filter out the ones labeled as Unclassified
filtered_pwy_abund_full2 = filtered_pwy_abund_full2[filtered_pwy_abund_full2["TaxGroup"]!='Unclassified']

In [26]:
#Calcuate aggregated metabolic pathway abundance across major taxonomic groups
agg_metab_pwy_abund_df = filtered_pwy_abund_full2.groupby('TaxGroup').sum()
#Sorted by max metabolic pathway activity
agg_metab_pwy_abund_df = agg_metab_pwy_abund_df.loc[agg_metab_pwy_abund_df.sum(axis=1).sort_values(ascending=False).index]
#Drop stations with 0 counts
agg_metab_pwy_abund_df = agg_metab_pwy_abund_df[agg_metab_pwy_abund_df.columns[agg_metab_pwy_abund_df.sum()>0]]
#Log-transform data
#agg_metab_pwy_abund_df = agg_metab_pwy_abund_df.applymap(lambda x:np.log10(x+1))

The following stacked barchart gives an overview of how the prevalence of different major plankton groups in terms of aggregated metabolic activity changes at different time points on a daily basis 

In [27]:
# n = len(['blue','blueviolet','aqua','#00C957',
#          'brown','greenyellow','red',
#          'black','pink','darkgreen','gold',
#          'grey','orange','red1'])
n = agg_metab_pwy_abund_df.index.unique().size
tax_groups_col_list = plt.cm.get_cmap('tab20b', n)

In [28]:
# color_list = sns.color_palette(None,n_colors=agg_metab_pwy_abund_df.index.shape[0])
fig, ax = plt.subplots(figsize=(20,10))
# tax_groups_col_list = plt.cm.get_cmap('jet_r', agg_metab_pwy_abund_df.shape[0])
# agg_metab_pwy_abund_df.T.plot.bar(stacked=True,ax=ax,colormap=tax_groups_col_list)
tax_groups_col_list = ['blue','blueviolet','aqua','#00C957',
                       'brown','greenyellow','red',
                       'black','pink','darkgreen','gold',
                       'grey','orange','green']

agg_metab_pwy_abund_df.T.plot(kind='bar', stacked=True, 
                              #cmap=tax_groups_col_list,
                              color=tax_groups_col_list, 
                              ax=ax
                              )
ax.legend(title=None, ncol=4, fontsize=15, bbox_to_anchor=(0.665,0.81))
ax.set_xlabel("Sampling time point (day:time)", fontsize=20)
ax.set_ylabel("Aggregated metabolic pathway abundance\nCounts per million mapped reads (Log-scale)", fontsize=20)
ax.set_yscale('log')
ax.tick_params(axis='both',labelsize =15)
sns.despine()
fig.show()

Now let's reshape the DF above in a way that can be used for creating a clustermap with pathway specific abundances aggregated across major plankton taxonomic groups 

In [29]:
from matplotlib.pyplot import gcf

In [30]:
df_cont = []
pwy_id_list = agg_pwy_abund.index[:10]
for pwy_id in pwy_id_list:
    #Here we get the pathway-specific abundance aggregated across broad taxonomic groups
    subdf = filtered_pwy_abund_full2.iloc[:,1:].loc[pwy_id]
    if(len(subdf.shape)==1):
        new_subdf = subdf.to_frame().T.reset_index().rename(columns={'index': 'PWY'})
        new_subdf["PWY"] = new_subdf["PWY"][0].split(": ")[-1].capitalize()
        df_cont.append(new_subdf.set_index(['PWY','TaxGroup']))
        #df_cont.append(subdf.to_frame().T.reset_index().rename(columns={'index': 'PWY'}).set_index(['PWY','TaxGroup']))
    else:
        pwy_specific_abund_profiles = subdf.groupby('TaxGroup').sum()
        pwy_specific_abund_profiles["PWY"] = pwy_id.split(": ")[-1].capitalize()
        df_cont.append(pwy_specific_abund_profiles.reset_index().set_index(['PWY','TaxGroup']))
        
#Finally, stack up dfs and create one single df with multi-index: pwy and taxonomic groups. Data is log-transformed
pwy_tax_indexed_df = pd.concat(df_cont).applymap(lambda x: np.log10(1+x))

In [31]:
#Create a list of colors for the pwy ids on the y axis
##pwy_col_list = sns.cubehelix_palette(pwy_id_list.size, light=.9, dark=.1, reverse=True, start=1, rot=-2)
pwy_col_list = sns.color_palette(palette='Paired', n_colors=pwy_id_list.size)
pwy_id_col_map = dict(zip(pwy_id_list.map(lambda s: s.split(": ")[-1].capitalize()), pwy_col_list))
pwy_id_colors = [pwy_id_col_map[k] for k in pwy_tax_indexed_df.index.get_level_values('PWY')]
#Generating colors for taxa
tax_id_col_map = dict(zip(agg_metab_pwy_abund_df.index,tax_groups_col_list))
tax_id_colors = pwy_tax_indexed_df.index.get_level_values('TaxGroup').map(tax_id_col_map)

In [32]:
#Here we create a multi-index DF to propely assign colors to rows in the clustermap
get_pwy_cont = []
get_tax_cont = []
pwy_id_col_cont = []
tax_id_col_cont = []
for idx in pwy_tax_indexed_df.index:
    get_pwy, get_tax = idx
    get_pwy_cont.append(get_pwy)
    get_tax_cont.append(get_tax)
    pwy_id_col_cont.append(pwy_id_col_map[get_pwy])
    tax_id_col_cont.append(tax_id_col_map[get_tax])
    
arrays = [get_pwy_cont, get_tax_cont]
pwy_taxa_color_df = pd.DataFrame(data=zip(pwy_id_col_cont,tax_id_col_cont), columns=['PWY', 'TaxGroup'],
                                 index=pd.MultiIndex.from_arrays(arrays, names=('PWY', 'TaxGroup')))

pwy_tax_indexed_df = pwy_tax_indexed_df[agg_metab_pwy_abund_df.columns]
# pwy_tax_indexed_df.index.names = [' ', ' ']

The following clustermap summarizes contributions by different taxonomic groups to metabolic pathway activities at different time points through the day, over 3 consecutive days. 

In [33]:
g = sns.clustermap(pwy_tax_indexed_df,
                   # Turn off the clustering
                   row_cluster=False, 
                   col_cluster=True,
                   metric=distance.braycurtis,
                   method="single",
                   # Add colored class labels using data frame created from node and network colors
                   row_colors = pwy_taxa_color_df,
                   col_colors = None,
                   # Make the plot look better when many rows/cols
                   linewidths=0.2,
                   xticklabels=True, 
                   yticklabels=False,
                   center=0, 
                   cmap="YlOrRd",
                   figsize=(10, 10), 
                   dendrogram_ratio=(0.2, 0.2),
                   cbar_kws = {
                               "label":"Counts per million mapped reads (Log-scale)",
                               "orientation":"vertical",
                               "shrink":0.1,
                               #"extend":"both", 
                               #"drawedges":True, 
                               #"extendfrac":0.01,
                               "ticks":np.arange(0,4)
                              }
                   )

g.ax_heatmap.set_ylabel(" ")

for label in pwy_id_col_map.keys():
    g.ax_col_dendrogram.bar(0, 0, color=pwy_id_col_map[label], label=label, 
                            linewidth=0, width=0.4)

l1 = g.ax_col_dendrogram.legend(title='PWY', loc="center", ncol=1, bbox_to_anchor=(0.025, 0.712), 
                                fontsize=8, bbox_transform=gcf().transFigure)


for label in tax_id_col_map.keys():
    g.ax_row_dendrogram.bar(0, 0, color=tax_id_col_map[label], label=label, 
                            linewidth=0, width=0.4)

l2 = g.ax_row_dendrogram.legend(title='TaxGroup', loc="center", ncol=2, bbox_to_anchor=(0.025, 0.53), 
                                fontsize=8, bbox_transform=gcf().transFigure)

g.cax.set_position([.965, .35, .03, .45])
#g.ax_heatmap.set_title("California Current plankton microbiome\n(BioProject accession number PRJNA320636)", fontsize=18)

plt.show()

Now let's zoom in into the Cyanobacteria group and plot a clade-specific clustermap

In [34]:
tax_specific_pwy_abund_df = filtered_pwy_abund_full2[filtered_pwy_abund_full2["TaxGroup"]=="Cyanobacteria"].iloc[:,:-1]
#Clean species label
tax_specific_pwy_abund_df['Species'] = tax_specific_pwy_abund_df['Species'].apply(lambda s: s.split(".s__")[-1].split("__")[0].replace("_"," "))
#Trim down index labels to make figure labels more readable
tax_specific_pwy_abund_df.index = tax_specific_pwy_abund_df.index.map(lambda s: s.split(": ")[-1].capitalize())
#Sort pwys based on total activity across all stations
pwy_sorted_by_total_abund = tax_specific_pwy_abund_df.sum(axis=1).reset_index().groupby("PWY").sum().sort_values(0,ascending=False)

#Get the list of unique species in the tax group under analysis
unique_species = tax_specific_pwy_abund_df['Species'].unique()
#Pick those stations where metabolic activity for the tax group in question is pretty high
sum_across_stations = tax_specific_pwy_abund_df.iloc[:,1:].sum()
set_stations = sum_across_stations[sum_across_stations>100].index.values
#Pick top 10 most abundant/active metabolic pathways
tax_specific_pwy_abund_df2 = tax_specific_pwy_abund_df.loc[pwy_sorted_by_total_abund.index.values[:10]]
#Log-scaled df
tax_specific_pwy_abund_df2 = tax_specific_pwy_abund_df2.reset_index().set_index(['PWY','Species'])[set_stations].applymap(lambda x: np.log10(1+x))

In [35]:
#Get list of pwys and species
top_pwy_list = tax_specific_pwy_abund_df2.index.get_level_values("PWY").drop_duplicates() 
#np.unique([i[0] for i in tax_specific_pwy_abund_df2.index.values])
#Set pwy color list
pwy_col_list2 = sns.color_palette(palette='Paired', n_colors=top_pwy_list.size)
pwy2color_dict = dict(zip(top_pwy_list,pwy_col_list2))

#Get species list and create colors
species_list = tax_specific_pwy_abund_df2.index.get_level_values("Species").drop_duplicates()
#np.unique([i[1] for i in tax_specific_pwy_abund_df2.index.values])
species_col_list = sns.color_palette(palette='tab20b', n_colors=species_list.size)
sps2color_dict = dict(zip(species_list,species_col_list))

In [36]:
#Now let's get the indexes properly linked to color codes
pwy_sps_col_cont = []
for p,s in tax_specific_pwy_abund_df2.index:
    pwy_sps_col_cont.append([pwy2color_dict[p], sps2color_dict[s]])
    
#finally we get the Multi-index df with color codes for the clustermap
pwy_species_color_df = pd.DataFrame(pwy_sps_col_cont, columns=["PWY","Species"], index=tax_specific_pwy_abund_df2.index)

The following is the Cyanobacteria-specific clustermap illustrating metabolic pathway abundance per specicies identified

In [37]:
g = sns.clustermap(tax_specific_pwy_abund_df2,
                   # Turn off the clustering
                   row_cluster=False, 
                   col_cluster=True,
                   metric=distance.braycurtis,
                   method="single",
                   # Add colored class labels using data frame created from node and network colors
                   row_colors = pwy_species_color_df,
                   col_colors = None,
                   # Make the plot look better when many rows/cols
                   linewidths=0.2,
                   xticklabels=True, 
                   yticklabels=False,
                   center=0, 
                   cmap="YlOrRd",
                   figsize=(10, 10), 
                   dendrogram_ratio=(0.2, 0.2),
                   cbar_kws = {
                               "label":"Counts per million mapped reads (Log-scale)",
                               "orientation":"vertical",
                               "shrink":0.1,
                               #"extend":"both", 
                               #"drawedges":True, 
                               #"extendfrac":0.01,
                               "ticks":np.arange(0,4)
                              }
                   )

g.ax_heatmap.set_ylabel(" ")

for label in top_pwy_list:
    g.ax_col_dendrogram.bar(0, 0, color=pwy2color_dict[label], label=label, 
                            linewidth=0, width=0.4)

l1 = g.ax_col_dendrogram.legend(title='PWY', loc="center", ncol=1, bbox_to_anchor=(-0.02, 0.735), 
                                fontsize=8, bbox_transform=gcf().transFigure)


for label in species_list:
    g.ax_row_dendrogram.bar(0, 0, color=sps2color_dict[label], label=label, 
                            linewidth=0, width=0.4)

l2 = g.ax_row_dendrogram.legend(title='Species', loc="center", ncol=1, bbox_to_anchor=(-0.02, 0.535), 
                                fontsize=8, bbox_transform=gcf().transFigure)

g.cax.set_position([.965, .35, .03, .45])
#g.ax_heatmap.set_title("California Current plankton microbiome\n(BioProject accession number PRJNA320636)", fontsize=18)

plt.show()

#### Calculate dist matrix (BC) and run MDS to visualize data points in high dimensional space (vectors of metabolic pathway abundance per species) as 2D projections

In [42]:
# mds_df = filtered_pwy_abund_full2.iloc[:,1:][pwy_tax_indexed_df.columns]
# #Compute distance matrix
# X = mds_df.T.values
# dist_matrix = np.zeros((X.shape[0],X.shape[0]))
# for i in np.arange(X.shape[0]):
#     for j in np.arange(X.shape[0]):
#         dist_matrix[i,j] = distance.braycurtis(X[i],X[j])

# #Replace nan with 0s
# dist_matrix = pd.DataFrame(dist_matrix).fillna(0).values        

# #Run MDS
# mds = MDS(dissimilarity='precomputed', random_state=0)
# # Get the embeddings
# X_transform = mds.fit_transform(dist_matrix)

In [43]:
# #Redefine lbls here
# lbls = mds_df.columns
# #Create a list of colors to uniquely identify each time point
# #unique_tps = pd.Series([s.split(':')[-1] for s in lbls]).unique()
# ucs_dict = dict(zip(lbls.map(lambda s: s.split("_")[0]).unique(),
#                     sns.color_palette(None,n_colors=lbls.shape[0])))
# color_list = []
# for lbl in lbls:
#     color_list.append(ucs_dict[lbl.split("_")[0]])

Visualize 2D projections of data points

In [1]:
# y = X_transform[:,0]
# z = X_transform[:,1]
# fig, ax = plt.subplots(figsize=(10,10))
# ax.scatter(y,z,c=color_list, s=100)
# for i, txt in enumerate(lbls):
#     ax.annotate(txt, (y[i]-0.06, z[i]+0.02), fontsize=9)
# #ax.set_xlim([-.5,.5])
# # ax.set_xticks([])
# # ax.set_yticks([])
# # ax.set_title('Bray-Curtis distance')
# ax.set_xlabel("MDS-1", fontsize=16)
# ax.set_ylabel("MDS-2", fontsize=16)
# sns.despine()
# fig.show()